<a href="https://colab.research.google.com/github/mfigueiro/Case_Elo/blob/main/Case_Elo.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [ ]:
import pandas as pd
import nltk as nlt
import numpy as np

In [ ]:
from google.colab import files

In [ ]:
files.upload()

Saving elo7_recruitment_dataset.csv to elo7_recruitment_dataset (1).csv


{'elo7_recruitment_dataset.csv': b'product_id,seller_id,query,search_page,position,title,concatenated_tags,creation_date,price,weight,express_delivery,minimum_quantity,view_counts,order_counts,category\n11394449,8324141,espirito santo,2,6,Mandala Esp\xc3\xadrito Santo,mandala mdf,2015-11-14 19:42:12,171.89,1200.0,1,4,244,,Decora\xc3\xa7\xc3\xa3o\n15534262,6939286,cartao de visita,2,0,Cart\xc3\xa3o de Visita,cartao visita panfletos tag adesivos copos long drink canecas,2018-04-04 20:55:07,77.67,8.0,1,5,124,,Papel e Cia\n16153119,9835835,expositor de esmaltes,1,38,Organizador expositor p/ 70 esmaltes,expositor,2018-10-13 20:57:07,73.920006,2709.0,1,1,59,,Outros\n15877252,8071206,medidas lencol para berco americano,1,6,Jogo de Len\xc3\xa7ol Ber\xc3\xa7o Estampado,t jogo lencol menino lencol berco,2017-02-27 13:26:03,118.770004,0.0,1,1,180,1.0,Beb\xc3\xaa\n15917108,7200773,adesivo box banheiro,3,38,ADESIVO BOX DE BANHEIRO,adesivo box banheiro,2017-05-09 13:18:38,191.81,507.0,1,6,34,,Decora

KeyboardInterrupt: ignored

In [ ]:
df = pd.read_csv("elo7_recruitment_dataset (1).csv")

In [ ]:

# Adaptado de: https://github.com/RenatoBMLR/nlpPy/tree/master/src


class TextDataset(object):

    def __init__(self, df, lang='english'):

        # Leitura e Download das palavras chaves
        from nltk import download
        download('stopwords')

        # Para as palavras chaves empregaremos as disponívels na biblioteca
        # ntlk
        from nltk.corpus import stopwords

        # Tokenização empregamos TweetTokenizer,
        # que considera palavra itens como outras ":)" e afins.
        # Além disso, pegamos as string com letra mínuscula.
        from nltk.tokenize import TweetTokenizer

        # Stremmer emprega será o Porter
        from nltk.stem import PorterStemmer

        # Lemmatizer empregado será a WordNet,
        # em uma proxíma versão do documento
        # espero escrever um descrição sobre ela.
        # Considera semântica para redução ao Lema

        from nltk.stem import WordNetLemmatizer

        # Motor para extração de atributos
        from sklearn.feature_extraction.text import TfidfTransformer, CountVectorizer

        self.data = df
        self.tokenizer = TweetTokenizer()

        stp = stopwords.words('english')
        from numpy import concatenate

        stp_ext = [
            'say',
            'says',
            'bloomberg',
            'podcast',
            'u',
            'radio',
            'u',
            'daybreak']
        stp_1 = list(concatenate([stp, stp_ext]))
        self.stop_words = set(stp_1)

        download('wordnet')
        #self.stop_words = set(stopwords.words(lang))
        self.lemmatizer = WordNetLemmatizer()
        self.ps = PorterStemmer()

        # passagem de ponteiro para só inicializarmos ele no método que usa.
        self.count_method = CountVectorizer
        self.feature_extractor = TfidfTransformer()

        self.tf_idf = []
        # guardar matriz esparsa
        self.idf = []

        self.lda = []
        self.svd = []
        self.nme = []

        # guarda agrupamento
        self.label_svd = []
        # guarda agrupamento
        self.label_nme = []
        # guarda agrupamento
        self.label_lda = []
        # guarda agrupamento
        self.label_idf = []

        # guarda método de agrupamento
        self.kmeans_svd = []
        # guarda método de agrupamento
        self.kmeans_nme = []
        # guarda método de agrupamento
        self.kmeans_lda = []
        # guarda método de agrupamento
        self.kmeans_idf = []

        # Parâmetros
        self.sem_pontuation = True
        self.sem_stop = True
        self.lemma = True
        self.stem = False

        self.seed = 42
        # NME
        self.n_components_nme = 10
        self.alpha = .1
        self.l1_ratio = .5
        self.init = 'nndsvd'
        # SVD
        self.n_components_svd = 500
        # LDA
        # CountVectorizer
        self.min_df = 3
        self.max_features = 100000
        self.analyzer = 'word'
        self.ngram_range = (1, 2)
        # LDA
        self.n_components_lda = 10
        self.learning_method = 'online'
        self.max_iter_lda = 10

        # Mini-KMeans
        self.n_clusters = 10
        self.n_init = 1
        self.init_size = 1000
        self.verbose = False
        self.max_iter = 1000

        # Sentiment
        download('vader_lexicon')
        from nltk.sentiment import SentimentIntensityAnalyzer
        self.sid = SentimentIntensityAnalyzer()

        # sub-label

        self.sub_label = []
        self.sub_method = []

    def _get_tokens(self, words):
        return [word.lower() for word in self.tokenizer.tokenize(words)]

    def _removeStopwords(self, words):
        # Removing all the stopwords
        return [word for word in words if word not in self.stop_words]

    def _removePonctuation(self, words):
        # bibliotecas usadas para substituição
        from re import sub
        return sub(r'[^\w\s]', '', words)

    def _lemmatizing(self, words):
        # Lemmatizing
        return [self.lemmatizer.lemmatize(word) for word in words]

    def _stemming(self, words):
        # Stemming
        return [self.ps.stem(word) for word in words]

    def process_data(self,
                     col='title',
                     remove_pontuation=True,
                     remove_stopw=True,
                     lemmalize=True,
                     stem=False):

        self.sem_pontuation = remove_pontuation
        self.sem_stop = remove_stopw
        self.lemma = lemmalize
        self.stem = stem

        self.data = self.data.drop_duplicates(
            subset=col, keep="last").reset_index(
            drop=True)

        proc_col = col
        if remove_pontuation:
            proc_col = col + '_data'
            self.data[proc_col] = self.data[col].apply(
                lambda x: self._removePonctuation(x))

        # get tokens of the sentence
        self.data[proc_col] = self.data[proc_col].apply(
            lambda x: self._get_tokens(x))

        if remove_stopw:
            self.data[proc_col] = self.data[proc_col].apply(
                lambda x: self._removeStopwords(x))
        if lemmalize:
            self.data[proc_col] = self.data[proc_col].apply(
                lambda x: self._lemmatizing(x))
        if stem:
            self.data[proc_col] = self.data[proc_col].apply(
                lambda x: self._stemming(x))

        self.data['number_words'] = self.data[proc_col].apply(lambda x: len(x))
        self.proc_col = proc_col

        # extraindo da classe text_tokens, o títulos com tokens processados.
        tokens = self.data[col + '_data']

        self.data[col +
                  '_joined'] = list(tokens.map(lambda tokens: " ".join(tokens)))

    def feature_transformation(self, col='title'):
        '''





        '''
        count_method = self.count_method(min_df=self.min_df,
                                         analyzer=self.analyzer,
                                         ngram_range=self.ngram_range,
                                         max_features=self.max_features,
                                         stop_words=self.stop_words)

        tf_idf_vec = self.feature_extractor

        # ajustamos o método de extração e transformamos a entrada
        self.count_vector = count_method.fit_transform(
            self.data[col + '_joined'])

        self.idf = tf_idf_vec.fit_transform(self.count_vector)

        self.count_method = count_method
        self.feature_extractor = tf_idf_vec

        self.data = self.data.reset_index(drop=True)



In [ ]:
return_data = TextDataset(df, lang='portuguese')

[nltk_data] Downloading package stopwords to /root/nltk_data...
[nltk_data]   Package stopwords is already up-to-date!
[nltk_data] Downloading package wordnet to /root/nltk_data...
[nltk_data]   Package wordnet is already up-to-date!
[nltk_data] Downloading package vader_lexicon to /root/nltk_data...
[nltk_data]   Package vader_lexicon is already up-to-date!


In [ ]:
return_data.process_data(col='query',
                     remove_pontuation=True,
                     remove_stopw=True,
                     lemmalize=True,
                     stem=False)

In [ ]:
return_data.feature_transformation(col='query') 

In [ ]:
#Fonte: https://www.geeksforgeeks.org/create-inverted-index-for-file-using-python/
estrutura_dados = {} 

for i, line in enumerate(return_data.data['query_data']): 

  for item in line: 

    if item in line: 
        if item not in estrutura_dados: 
            estrutura_dados[item] = [] 

        if item in estrutura_dados: 
            estrutura_dados[item].append(i+1) 

In [ ]:
def search_engine(palavra, base, data):
  lista = base[palavra]
  menor_indice = np.inf
  for indice in lista:
    if menor_indice > data['search_page'][indice]:
      menor_indice = indice
  
  return menor_indice



In [ ]:
 indice = search_engine(palavra="fotografico", 
                        base=estrutura_dados, data=return_data.data)

In [ ]:
return_data.data.iloc[indice-1]

product_id                                                    10890162
seller_id                                                      5016210
query                                   fundo fotografico dia dos pais
search_page                                                          1
position                                                            10
title                Fundo Fotográfico em Tecido 170x250cm - Dia do...
concatenated_tags                                             dia pais
creation_date                                      2019-06-07 12:41:13
price                                                           170.45
weight                                                             441
express_delivery                                                     1
minimum_quantity                                                     1
view_counts                                                         84
order_counts                                                         1
catego